In [2]:
import re
import string
import graphlab as gl
import pandas as pd
import funcy as fp
import pyLDAvis
import pyLDAvis.graphlab

gl.set_runtime_config('GRAPHLAB_DEFAULT_NUM_PYLAMBDA_WORKERS', 24)
pyLDAvis.enable_notebook()

In [3]:
stories_sf = gl.load_sframe("hn_processed.sframe")

In [4]:
import spacy.parts_of_speech as pos

DEFAULT_POS = set([pos.NOUN, pos.VERB, pos.ADV, pos.ADJ])
DEFAULT_STOPWORDS = gl.text_analytics.stopwords() | set(['pm','am', "'re", "'ve", "n't", 'thing'])

In [7]:
from gensim.corpora import Dictionary

In [8]:
unfiltered_dictionary = Dictionary.load('unfiltered.dict')

[INFO] loading Dictionary object from unfiltered.dict


In [14]:
from copy import deepcopy

def filter_dict(no_below=5, no_above=0.5, keep_n=None, bad_tokens=None, good_tokens=None, orig_dict=unfiltered_dictionary):
    dictionary = deepcopy(orig_dict)
    def tokens2ids(words):
        if words: return [unfiltered_dictionary.token2id[w] for w in words]
    if good_tokens or bad_tokens:        
        dictionary.filter_tokens(bad_ids=tokens2ids(bad_words), good_ids=tokens2ids(good_words))
        dictionary.compactify()
    dictionary.filter_extremes(no_below=no_below, no_above=no_above, keep_n=keep_n)
    dictionary.compactify()
    return dictionary

In [15]:
%%time
dictionary = filter_dict(no_below=10, no_above=0.3, keep_n=100000)

[INFO] discarding 552490 tokens: [(u'mr._costolo', 2), (u'gaillard/reuters', 1), (u'rob_glaser', 8), (u'black_cab', 8), (u'leo_kelion_technology', 7), (u'london_taxi', 4), (u'kalanick', 6), (u'tfl', 5), (u'bertram', 9), (u'ltda', 3)]...
[INFO] keeping 67069 tokens which were in no less than 10 and no more than 76191 (=30.0%) documents
[INFO] resulting dictionary: Dictionary(67069 unique tokens: [u'fawn', u'aishwarya_rai', u'joi_ito', u'mainly_consist', u'python_interpreter']...)


CPU times: user 5.58 s, sys: 97.3 ms, total: 5.68 s
Wall time: 5.61 s


In [16]:
def doc2bags(dictionary, doc):  
    return {dictionary[id]: count for id, count in dictionary.doc2bow(doc)}    

In [17]:
%%time
bows = stories_sf["processed"].apply(fp.partial(doc2bags, dictionary))

CPU times: user 1.6 s, sys: 147 ms, total: 1.74 s
Wall time: 3 s


In [18]:
%%time
tm_cgs = gl.topic_model.create(bows, num_topics=100, num_iterations=10, method='cgs')

PROGRESS: Learning a topic model
PROGRESS:        Number of documents    253973
PROGRESS:            Vocabulary size     67069
PROGRESS:    Running collapsed Gibbs sampling
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | Iteration | Elapsed Time  | Tokens/Second  | Est. Perplexity |
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | 10        | 51.06s        | 2.36102e+06    | 0               |
PROGRESS: +-----------+---------------+----------------+-----------------+
CPU times: user 111 ms, sys: 14.7 ms, total: 126 ms
Wall time: 1min 12s


In [19]:
%%time
pyLDAvis.graphlab.prepare(tm_cgs, bows)

CPU times: user 56.3 s, sys: 1.81 s, total: 58.1 s
Wall time: 1min 50s


PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
87     1.602218        1       1 -0.171738  0.119725
10     1.504014        1       2 -0.165393  0.128636
26     1.489069        1       3 -0.196111  0.093012
9      1.481865        1       4  0.172816  0.051665
94     1.455577        1       5  0.104114  0.136156
69     1.447185        1       6  0.146391  0.142630
44     1.423206        1       7  0.070349  0.108779
24     1.398496        1       8  0.048496  0.163250
6      1.374463        1       9 -0.055555  0.168794
4      1.364507        1      10  0.086933 -0.094992
76     1.356384        1      11  0.050899  0.096560
64     1.343536        1      12  0.121508  0.073312
14     1.332915        1      13  0.015486  0.038999
79     1.331865        1      14 -0.191840  0.052308
40     1.314062        1      15  0.121317  0.088013
1      1.290488        1      16 -0.122652  0.141513
30     1.275478        1      17  0.128717  0.112166
15     1.256625        1      18  0.099606  0.081505
42     1.238057        1      19  0.144914 -0.071624
41     1.233597        1      20  0.032770  0.140759
73     1.233445        1      21 -0.106929  0.122894
3      1.208500        1      22  0.123529  0.040038
90     1.176994        1      23 -0.191258  0.014093
60     1.153851        1      24  0.103568  0.063928
28     1.151196        1      25 -0.142620  0.031071
68     1.150961        1      26 -0.031241  0.143055
77     1.143123        1      27  0.152482 -0.133842
97     1.124169        1      28 -0.165393 -0.013361
49     1.109561        1      29  0.051428  0.011747
25     1.100339        1      30 -0.155046 -0.158467
...         ...      ...     ...       ...       ...
32     0.873992        1      71  0.037524 -0.018625
54     0.872816        1      72  0.099720  0.009342
37     0.872638        1      73  0.043328  0.028017
45     0.869057        1      74 -0.057957  0.019340
23     0.866365        1      75 -0.007913  0.024866
21     0.833703        1      76 -0.012808  0.008962
58     0.810823        1      77 -0.031001 -0.065439
70     0.785844        1      78 -0.098145 -0.119561
51     0.784411        1      79  0.065419 -0.070800
33     0.781931        1      80  0.002077  0.006390
74     0.778352        1      81  0.046410 -0.052071
65     0.768839        1      82  0.041316 -0.101299
29     0.746337        1      83 -0.067204 -0.077968
78     0.728913        1      84  0.098918 -0.118530
71     0.724682        1      85  0.063704 -0.042745
38     0.718598        1      86  0.018407 -0.028310
35     0.717174        1      87  0.088822 -0.065459
83     0.714450        1      88  0.025167 -0.092989
31     0.711066        1      89  0.015838  0.001345
55     0.702092        1      90  0.049421 -0.084335
12     0.700982        1      91  0.024634 -0.101248
81     0.700310        1      92  0.015773 -0.064957
5      0.693146        1      93  0.005483 -0.023859
36     0.677799        1      94  0.043864  0.016974
17     0.670481        1      95  0.068051 -0.175434
7      0.653159        1      96 -0.081829 -0.133933
19     0.641771        1      97 -0.008864 -0.082479
18     0.609821        1      98 -0.025804 -0.103665
52     0.598072        1      99  0.084631 -0.076530
98     0.591726        1     100  0.019421 -0.089751

[100 rows x 5 columns], topic_info=       Category           Freq               Term   Total  loglift  logprob
2194    Default   72314.000000            company   72314  30.0000  30.0000
23748   Default   67171.000000               user   67171  29.0000  29.0000
54649   Default   96957.000000               work   96957  28.0000  28.0000
17555   Default   94198.000000             people   94198  27.0000  27.0000
42576   Default  108039.000000               make  108039  26.0000  26.0000
62222   Default   89625.000000               time   89625  25.0000  25.0000
61587   Default   43571.000000             google   43571  24.

In [20]:
dictionary = filter_dict(no_below=5, no_above=0.3)
bows = stories_sf["processed"].apply(fp.partial(doc2bags, dictionary))

[INFO] discarding 503561 tokens: [(u'mr._costolo', 2), (u'gaillard/reuters', 1), (u'london_taxi', 4), (u'ltda', 3), (u'confusables', 1), (u'confusable', 4), (u'utr', 1), (u'chgrp', 4), (u'runhost', 1), (u'filemap', 1)]...
[INFO] keeping 115998 tokens which were in no less than 5 and no more than 76191 (=30.0%) documents
[INFO] resulting dictionary: Dictionary(115998 unique tokens: [u'fawn', u'unsupportable', u'joi_ito', u'mainly_consist', u'sonja']...)


In [23]:
topic_model100 = gl.topic_model.create(bows, num_topics=100, num_iterations=200)

PROGRESS: Learning a topic model
PROGRESS:        Number of documents    253973
PROGRESS:            Vocabulary size    115998
PROGRESS:    Running collapsed Gibbs sampling
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | Iteration | Elapsed Time  | Tokens/Second  | Est. Perplexity |
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | 10        | 55.15s        | 2.49533e+06    | 0               |
PROGRESS: | 20        | 1m 42s        | 2.55197e+06    | 0               |
PROGRESS: | 30        | 2m 29s        | 2.42161e+06    | 0               |
PROGRESS: | 40        | 3m 17s        | 2.40682e+06    | 0               |
PROGRESS: | 50        | 4m 4s         | 2.51469e+06    | 0               |
PROGRESS: | 60        | 4m 51s        | 2.4741e+06     | 0               |
PROGRESS: | 70        | 5m 38s        | 2.47171e+06    | 0               |
PROGRESS: | 80        | 6m 26s        | 2.37051e+06    | 0               |
PR

In [24]:
%%time
vis_data100 = pyLDAvis.graphlab.prepare(topic_model100, bows)

CPU times: user 3min 31s, sys: 7.04 s, total: 3min 38s
Wall time: 5min 10s


/home/local/SAVVYSHERPA/bmabey/.virtualenvs/data/local/lib/python2.7/site-packages/skbio/stats/ordination/_principal_coordinate_analysis.py:107: RuntimeWarning: The result contains negative eigenvalues. Please compare their magnitude with the magnitude of some of the largest positive eigenvalues. If the negative ones are smaller, it's probably safe to ignore them, but if they are large in magnitude, the results won't be useful. See the Notes section for more details. The smallest eigenvalue is -0.00591032736493 and the largest is 1.11497827866.
  RuntimeWarning


In [31]:
vis_data100

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
30     2.287611        1       1 -0.129647  0.087757
64     2.124373        1       2  0.076708  0.224064
65     1.700713        1       3 -0.250556  0.014536
80     1.592263        1       4 -0.276779  0.153229
52     1.546258        1       5 -0.026924  0.187959
58     1.506463        1       6 -0.056366 -0.033566
66     1.468854        1       7  0.044781  0.174874
50     1.463340        1       8 -0.068105  0.094988
16     1.431524        1       9  0.056817  0.217159
8      1.363299        1      10  0.032897 -0.049823
20     1.335215        1      11 -0.062375 -0.100794
59     1.334178        1      12  0.009054  0.182536
4      1.325628        1      13 -0.124980 -0.039228
34     1.325544        1      14 -0.279085  0.041224
86     1.301157        1      15  0.098954  0.201502
97     1.293074        1      16  0.006779  0.062349
9      1.293069        1      17 -0.015041 -0.138671
60     1.247991        1      18 -0.222528  0.079632
5      1.245604        1      19 -0.025394  0.141610
21     1.239364        1      20  0.020085 -0.059100
51     1.213053        1      21  0.006286  0.037625
2      1.213023        1      22 -0.059664 -0.044228
38     1.189150        1      23  0.020197 -0.103193
11     1.174390        1      24 -0.033626  0.047271
1      1.154885        1      25  0.011257 -0.042451
92     1.145478        1      26 -0.246584  0.066875
78     1.132684        1      27  0.119358  0.143844
79     1.129903        1      28  0.126711  0.048257
18     1.127339        1      29 -0.009729  0.134387
12     1.124085        1      30  0.158152  0.134929
...         ...      ...     ...       ...       ...
44     0.827939        1      71  0.004522 -0.070077
76     0.826214        1      72  0.167912 -0.030870
41     0.819532        1      73  0.070453  0.004141
39     0.814739        1      74 -0.082952 -0.066112
99     0.814434        1      75  0.053414 -0.168076
26     0.800158        1      76 -0.176698  0.036315
54     0.791526        1      77  0.104137  0.006325
75     0.780097        1      78  0.038667 -0.108507
70     0.778727        1      79  0.043130 -0.004027
82     0.776135        1      80 -0.105793  0.084949
43     0.774417        1      81 -0.023453 -0.089740
28     0.770047        1      82 -0.227967  0.058388
62     0.763620        1      83 -0.144380 -0.031235
83     0.759532        1      84 -0.003962 -0.110961
77     0.750799        1      85  0.115143 -0.068920
84     0.728582        1      86 -0.024190 -0.024294
7      0.711803        1      87  0.080842 -0.052130
95     0.692092        1      88 -0.015305 -0.027885
0      0.663805        1      89  0.066281 -0.034360
81     0.656808        1      90 -0.042162  0.026561
42     0.646800        1      91  0.053403 -0.120865
68     0.613605        1      92  0.035097 -0.140021
37     0.592735        1      93 -0.056220 -0.029440
56     0.588261        1      94  0.148834 -0.134348
24     0.550999        1      95  0.067392 -0.160357
29     0.521188        1      96  0.039503 -0.098335
35     0.509775        1      97  0.086785 -0.154182
33     0.486488        1      98  0.064344 -0.144135
27     0.472603        1      99 -0.031002 -0.123785
93     0.414565        1     100  0.028870 -0.113190

[100 rows x 5 columns], topic_info=        Category           Freq                     Term   Total  loglift  \
14784    Default   42831.000000                   ask_hn   42831  30.0000   
111186   Default   43571.000000                   google   43571  29.0000   
93464    Default   55306.000000                     data   55306  28.0000   
91192    Default   94198.000000                   people   94198  27.0000   
1900     Default   72314.000000                  company   72314  26.0000   
47035    Default   96957.000000                     work   96957  25.0000   
27068    Default   40389.000000                   desig

In [26]:
topic_model75 = gl.topic_model.create(bows, num_topics=75, num_iterations=200)

PROGRESS: Learning a topic model
PROGRESS:        Number of documents    253973
PROGRESS:            Vocabulary size    115998
PROGRESS:    Running collapsed Gibbs sampling
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | Iteration | Elapsed Time  | Tokens/Second  | Est. Perplexity |
PROGRESS: +-----------+---------------+----------------+-----------------+
PROGRESS: | 10        | 45.43s        | 2.89845e+06    | 0               |
PROGRESS: | 20        | 1m 25s        | 2.78779e+06    | 0               |
PROGRESS: | 30        | 2m 5s         | 2.98204e+06    | 0               |
PROGRESS: | 40        | 2m 46s        | 2.91351e+06    | 0               |
PROGRESS: | 50        | 3m 27s        | 2.84212e+06    | 0               |
PROGRESS: | 60        | 4m 8s         | 2.87685e+06    | 0               |
PROGRESS: | 70        | 4m 49s        | 2.95537e+06    | 0               |
PROGRESS: | 80        | 5m 30s        | 2.72292e+06    | 0               |
PR

In [27]:
%%time
vis_data75 = pyLDAvis.graphlab.prepare(topic_model75, bows)

CPU times: user 2min 58s, sys: 6.12 s, total: 3min 4s
Wall time: 4min 20s


In [32]:
vis_data75

PreparedData(topic_coordinates=           Freq  cluster  topics         x         y
topic                                               
66     2.422834        1       1  0.071812 -0.129958
64     2.259274        1       2 -0.103162 -0.204403
60     2.115144        1       3  0.154053  0.031207
28     2.052298        1       4  0.058636 -0.182065
52     1.994761        1       5  0.006648  0.086172
23     1.956870        1       6 -0.070203 -0.226255
43     1.901095        1       7  0.152462 -0.031857
50     1.873637        1       8  0.246645 -0.079020
42     1.867441        1       9  0.076125  0.046853
54     1.849482        1      10  0.271879 -0.058979
27     1.751327        1      11  0.200869 -0.099774
74     1.750452        1      12  0.014613  0.002248
73     1.688131        1      13  0.075188  0.087002
17     1.657115        1      14  0.034923 -0.021370
56     1.640423        1      15  0.015195 -0.161719
44     1.577586        1      16  0.008662  0.000370
26     1.558593        1      17  0.269697 -0.115034
48     1.534590        1      18  0.065139  0.133106
19     1.525035        1      19 -0.016145  0.068136
53     1.518868        1      20 -0.170219 -0.146664
34     1.517186        1      21 -0.060186 -0.107216
65     1.516550        1      22  0.018602 -0.184573
63     1.512829        1      23  0.054361  0.127544
0      1.493216        1      24 -0.060183 -0.110612
12     1.425072        1      25 -0.105728 -0.060732
38     1.424577        1      26 -0.153820 -0.155844
6      1.410291        1      27  0.076294  0.059024
32     1.395380        1      28 -0.050910  0.029332
21     1.392853        1      29  0.047803  0.060811
69     1.388321        1      30  0.065570  0.076740
...         ...      ...     ...       ...       ...
4      1.218425        1      46  0.216518 -0.087268
61     1.207034        1      47  0.057382  0.097898
67     1.190468        1      48 -0.002801 -0.019055
55     1.178911        1      49  0.023762  0.059008
30     1.169369        1      50 -0.125055 -0.026007
72     1.164986        1      51  0.101900 -0.038013
15     1.156104        1      52  0.063339  0.093820
39     1.151258        1      53 -0.004164  0.068164
9      1.143594        1      54  0.047872  0.055059
71     1.136876        1      55 -0.022821  0.154784
14     1.136788        1      56 -0.008676  0.034400
36     1.121394        1      57 -0.111028  0.061897
8      1.112280        1      58 -0.163349  0.045527
70     1.082262        1      59 -0.071529  0.112916
57     1.053476        1      60 -0.143809 -0.110440
25     1.012003        1      61 -0.048169 -0.005111
35     1.008488        1      62 -0.064470  0.086706
31     0.959532        1      63 -0.087922  0.092812
1      0.956576        1      64  0.020900 -0.000461
5      0.951535        1      65 -0.015350  0.025598
24     0.806341        1      66 -0.126933  0.143401
47     0.794417        1      67  0.077586  0.022563
3      0.773493        1      68 -0.044018  0.175012
46     0.736598        1      69 -0.029726  0.167249
49     0.722643        1      70 -0.014620  0.191158
2      0.709767        1      71  0.142926  0.081991
7      0.674477        1      72 -0.039608  0.145467
40     0.641636        1      73 -0.015931  0.114268
59     0.628936        1      74  0.048453  0.107058
13     0.626755        1      75 -0.055648  0.154839

[75 rows x 5 columns], topic_info=       Category           Freq             Term   Total  loglift  logprob
14784   Default   42831.000000           ask_hn   42831  30.0000  30.0000
111186  Default   43571.000000           google   43571  29.0000  29.0000
91192   Default   94198.000000           people   94198  28.0000  28.0000
1900    Default   72314.000000          company   72314  27.0000  27.0000
93464   Default   55306.000000             data   55306  26.0000  26.0000
47035   Default   96957.000000             work   96957  25.0000  25.0000
27068   Default   40389.000000           design   40389  24.0000  24.0000
929